<span style="display:block;text-align:center;margin-right:105px"><img src="../media/logos/hacks-logo.png" width="200"/></span>

## Table of Contents

<ul>
    <li><a href='#Dependencies'>Dependencies</a></li>
    </li>
    <li><a href='#Modelling'>Modelling</a>
        <ol style='margin-top: 0em;'>
            <li><a href='#1.-State-Variables'>State Variables</a></li>
            <li><a href='#2.-System-Parameters'>System Parameters</a></li>
            <li><a href='#3.-Policy-Functions'>Policy Functions</a></li>
            <li><a href='#4.-State-Update-Functions'>State Update Functions</a></li>
            <li><a href='#5.-Partial-State-Update-Blocks'>Partial State Update Blocks</a></li>
        </ol>
    </li>
    <li><a href='#Simulation'>Simulation</a>
        <ol style='margin-top: 0em;' start="6">
            <li><a href='#6.-Configuration'>Configuration</a></li>
            <li><a href='#7.-Execution'>Execution</a></li>
            <li><a href='#8.-Output-Preparation'>Output Preparation</a></li>
            <li><a href='#9.-Analysis'>Analysis</a></li>
        </ol>
    </li>
</ul>

---

# Dependencies

In [1]:
# cadCAD standard dependencies

# cadCAD configuration modules
from cadCAD.configuration.utils import config_sim
from cadCAD.configuration import Experiment

# cadCAD simulation engine modules
from cadCAD.engine import ExecutionMode, ExecutionContext
from cadCAD.engine import Executor

# cadCAD global simulation configuration list
from cadCAD import configs

# Included with cadCAD
import pandas as pd

# Additional dependencies

# For analytics
import numpy as np
rng = np.random.default_rng(42)

# For visualization
import panel as pn
import plotly.express as px
pd.options.plotting.backend = "plotly"

# From our model
from parameterized.funds import Funds
from parameterized.proposal_inverter import Wallet
from parameterized.whitelist_mechanism import NoVote

# Modelling

* Have a pool of the agents, like a dictionairy
* Have a pool of proposals, like a dictionairy
* Track the connections between the agents and the PI

The wallets are initialized with random funds.   
Let's start the simulation with 1,000,000 Funds, 100 wallets, 0 owners, 0 proposals, 0 brokers, 0 payers.  
Scenario 1: Largest 20% of wallets become owners.    
Scenario 2: All wallets have an equal chance of becoming owners.

Some wallets will become owners  
1,000,000 Funds, 100 Wallets, 10 Owners, 10 Proposal, 0 Brokers, 0 Payers

Some Brokers Join Proposals and some Payers join proposals  
1,000,000 Funds, 100 Wallets, 10 Owners, 10 Proposal, 7 Brokers, 5 Payers

On every step of the simulation, as an agent (Wallet) I have three considerations to make (3-action space)
1. Become an Owner and start a new Proposal
2. For each proposal, consider if I want to become a payer
3. For each proposal, consider if I want to become a broker
4. If I am a broker, I can make a claim on the proposals that I am a broker on
5. If I am an owner, I can cancel a proposal

Note for implementation. Pools of agents and wallets to be 'global' outside of the simulation state, and referenced as we go. 

## 1. State Variables

The simulation maintains a constant number of funds in the economy and a constant number of wallets that act as agents. Each wallet begins with a random amount of funds that have been distributed from the total.

Over time, the agents will deploy, contribute to, or join proposals, and this will increase the number of owners, payers, and brokers, respectively.

### 1.1 Initial State

In [2]:
initial_state = {
    # Initial conditions of the system
    'total_funds': 500_000,
    "wallet_funds": 500_000,
    "proposal_funds": 0,
    "n_wallets": 50,
    "n_proposals": 0,
    
    # Distribution of agent actions
    'owners': 0,
    'payers': 0,
    'brokers': 0,
    
    # Proposal properties
    "funds_staked": 0,
    "funds_claimed": 0,
    "funds_contributed": 0,
}

### 1.2 Global Variables

In [3]:
# These are the global variables representing the pool of wallets and pool of proposals
WALLETS = dict()
PROPOSALS = dict()
TRANSACTIONS = list() # columns=["timestep", "wallet", "wallet_funds", "action", "proposal", "proposal_funds"]

funds_distribution = rng.random(size=initial_state["n_wallets"])
funds_distribution = funds_distribution / np.sum(funds_distribution) * initial_state["total_funds"]

for funds in funds_distribution:
    wallet = Wallet(funds={"USD": funds})
    wallet.feature_vector = rng.uniform(size=wallet.number_of_features)
    WALLETS[wallet.public] = wallet
    
    TRANSACTIONS.append({
        "timestep": 0,
        "wallet": wallet.public,
        "wallet_funds": wallet.funds.total_funds(),
        "action": "initialize",
    })

## 2. System Parameters

Each of the actions and the hyperparameters of each action can be represented as a function that samples from some probability distribution.

- For the actions, the function should return a boolean, indicating whether or not an agent will perform this action during the current epoch.
- For the hyperparameters, the functions should return the value of the hyperparameter.

In [4]:
def feature_noise(n_features=5):
    return rng.normal(loc=0, scale=0.1, size=5)

### 2.1 Action Space Functions

Each action space function represents an agent's decision to perform an action. They should return `True` if the agent decides to perform the action, and `False` otherwise.

These functions are called in the policy functions, but kept separate for easy plug and play for different agent behaviours.

In [5]:
def a_static_0_percent(wallet: Wallet, n_proposals: int) -> list[bool]:
    """Returns `True` with a probability of 0%. In other words, `False` with a probability of 100%."""
    return np.full(shape=n_proposals, fill_value=False)

def a_static_1_percent(wallet: Wallet, n_proposals: int) -> list[bool]:
    """Returns `True` with a probability of 1%."""
    return rng.uniform(size=n_proposals) < 0.01

def a_static_50_percent(wallet: Wallet, n_proposals: int) -> list[bool]:
    """Returns `True` with a probability of 50%."""
    return rng.uniform(size=n_proposals) < 0.5

def a_static_100_percent(wallet: Wallet, n_proposals: int) -> list[bool]:
    """Returns `True` with a probability of 100%."""
    return np.full(shape=n_proposals, fill_value=True)

def a_dynamic_joined(wallet: Wallet, n_proposals: int, pr: float) -> list[bool]:
    """Returns `True` with a specified probability for all proposals this wallet has joined."""
    return np.array([rng.random() < pr if wallet.public in proposal.broker_agreements.keys() else False for proposal in PROPOSALS.values()])

def a_dynamic_funded(wallet: Wallet, n_proposals: int, pr: float) -> list[bool]:
    """Returns `True` with a specified probability for all proposals this wallet has funded."""
    return np.array([rng.random() < pr if wallet.public in proposal.payer_agreements.keys() else False for proposal in PROPOSALS.values()])

def a_decreasing_linear(wallet: Wallet, n_proposals: int, y_scale: float=1) -> list[bool]:
    """Based on a linear distribution where lower funds means a higher probability of joining."""
    max_funds = np.max([w.funds.total_funds() for w in WALLETS.values()])
    pr = y_scale * (-wallet.funds.total_funds() / max_funds + 1)
    
    return rng.uniform(size=n_proposals) < pr

def a_increasing_linear(wallet: Wallet, n_proposals: int, y_scale: float=1) -> list[bool]:
    """Based on a linear distribution where higher funds means a higher probability of paying."""
    max_funds = np.max([w.funds.total_funds() for w in WALLETS.values()])
    pr = y_scale * (wallet.funds.total_funds() / max_funds)
    
    return rng.uniform(size=n_proposals) < pr

def a_normal(wallet: Wallet, n_proposals: int, y_scale: float=1) -> list[bool]:
    """Based on a normal Gaussian distribution with the mean funds as the centre."""
    mean_funds = np.mean([w.funds.total_funds() for w in WALLETS.values()])
    max_funds = np.max([w.funds.total_funds() for w in WALLETS.values()])
    pr = y_scale * np.exp(-0.5 * np.power((wallet.funds.total_funds() - mean_funds) / (max_funds / 3), 2))
    
    return rng.uniform(size=n_proposals) < pr

def a_probability(wallet: Wallet, n_proposals: int, y_scale: float=1) -> list[bool]:
    """Based on the highest probability from the result of matrix factorization."""
    p_matrix = [proposal.feature_vector for proposal in PROPOSALS.values() if not proposal.cancelled]
    prs = np.matmul(p_matrix, wallet.feature_vector)
    
    return rng.uniform(size=n_proposals) < prs

### 2.2 Hyperparameter Functions

The hyperparameter functions represent the specifics of each action the agent may perform. For example, if the agent decides to join a proposal, then the agent must also decide how much to stake. A hypyerparameter function is then defined to decide how much to stake.

These functions are called in the policy functions, but kept separate for easy plug and play for different agent behaviours.

In [6]:
def h_join_stake(wallet: Wallet) -> Funds:
    return Funds({"USD": 10})

def h_pay_contribution(wallet: Wallet) -> Funds:
    return Funds({"USD": 50})

def h_vote_broker(wallet: Wallet) -> int:
    return rng.choice(list(WALLETS.keys()))

def h_vote_result(wallet: Wallet) -> bool:
    return True

def h_deploy_initial_funds(wallet: Wallet) -> Funds:
    return Funds({"USD": 100})

### 2.3 System Parameters

In [7]:
system_params = {
    "feature_noise": [feature_noise],
    
    # Probabilities defining the action space
    "join": [a_decreasing_linear],
    "claim": [a_dynamic_joined],
    "leave": [a_static_1_percent],
    "pay": [a_increasing_linear],
    "vote": [a_dynamic_funded],
    "deploy": [a_normal],
    "cancel": [a_static_0_percent],
    
    # The hyperparameters of each action
    "join_stake": [h_join_stake],

    "pay_contribution": [h_pay_contribution],

    "vote_broker": [h_vote_broker],
    "vote_result": [h_vote_result],
    
    "deploy_initial_funds": [h_deploy_initial_funds],
}

## 3. Policy Functions

The policy functions carry out the actions of each agent and will return a dictionary that contains a summary or aggregate function of the actions that have taken place during the current epoch.

In [8]:
def p_free_memory(params, substep, state_history, previous_state):
    """Destroys the memory of some objects in the last timestep.
    
    https://community.cadcad.org/t/working-with-large-objects/215/2
    """
    if previous_state["timestep"] > 0:
        for variable in params["global"]:
            state = state_history[-1]
            
            for substate in state:
                substate[key] = None
                
    return dict()


def p_iter_epoch(params, substep, state_history, previous_state):
    for proposal in PROPOSALS.values():
        proposal.iter_epoch()
        
    print(f"Epoch: {previous_state['timestep']}")
        
    return dict()


def p_iter_features(params, substep, state_history, previous_state):
    for wallet in WALLETS.values():
        wallet.feature_vector += params["feature_noise"]()
        
    for proposal in PROPOSALS.values():
        proposal.feature_vector += params["feature_noise"]()
        
    return dict()


def p_join(params, substep, state_history, previous_state):
    n_joined = 0
    funds_staked = 0
    
    for wallet in WALLETS.values():
        for proposal in np.extract(params["join"](wallet, len(PROPOSALS), y_scale=0.05), list(PROPOSALS.values())):
            stake = params["join_stake"](wallet)
            
            wallet_funds_old = wallet.funds.total_funds()
            proposal_funds_old = (proposal.funds + proposal.stake).total_funds()
            wallet = proposal.join(wallet, stake)
            wallet_funds_new = wallet.funds.total_funds()
            
            if wallet_funds_new != wallet_funds_old:
                transaction = {
                    "timestep": previous_state["timestep"],
                    "wallet": wallet.public,
                    "wallet_funds_old": wallet_funds_old,
                    "wallet_funds": wallet_funds_new,
                    "action": "join",
                    "proposal": proposal.public,
                    "proposal_funds_old": proposal_funds_old,
                    "proposal_funds": (proposal.funds + proposal.stake).total_funds(),
                }

                TRANSACTIONS.append(transaction)

                n_joined += 1
                funds_staked += wallet_funds_old - wallet_funds_new
            
    return {
        "n_joined": n_joined,
        "funds_staked": funds_staked,
    }
            
    
def p_claim(params, substep, state_history, previous_state):
    n_claimed = 0
    funds_claimed = 0
    
    for wallet in WALLETS.values():
        for proposal in np.extract(params["claim"](wallet, len(PROPOSALS), 1), list(PROPOSALS.values())):
            wallet_funds_old = wallet.funds.total_funds()
            proposal_funds_old = (proposal.funds + proposal.stake).total_funds()
            
            wallet = proposal.claim(wallet)
            wallet_funds_new = wallet.funds.total_funds()
            
            if wallet_funds_new != wallet_funds_old:
                transaction = {
                    "timestep": previous_state["timestep"],
                    "wallet": wallet.public,
                    "wallet_funds_old": wallet_funds_old,
                    "wallet_funds": wallet_funds_new,
                    "action": "claim",
                    "proposal": proposal.public,
                    "proposal_funds_old": proposal_funds_old,
                    "proposal_funds": (proposal.funds + proposal.stake).total_funds(),
                }

                TRANSACTIONS.append(transaction)

                n_claimed += 1
                funds_claimed += wallet_funds_new - wallet_funds_old
            
    return {
        "n_claimed": n_claimed,
        "funds_claimed": funds_claimed,
    }


def p_leave(params, substep, state_history, previous_state):
    n_left = 0
    funds_claimed = 0
    
    for wallet in WALLETS.values():
        for proposal in np.extract(params["leave"](wallet, len(PROPOSALS)), list(PROPOSALS.values())):
            wallet_funds_old = wallet.funds.total_funds()
            proposal_funds_old = (proposal.funds + proposal.stake).total_funds()
            
            wallet = proposal.leave(wallet)
            wallet_funds_new = wallet.funds.total_funds()
            
            if wallet_funds_new != wallet_funds_old:
                transaction = {
                    "timestep": previous_state["timestep"],
                    "wallet": wallet.public,
                    "wallet_funds_old": wallet_funds_old,
                    "wallet_funds": wallet_funds_new,
                    "action": "leave",
                    "proposal": proposal.public,
                    "proposal_funds_old": proposal_funds_old,
                    "proposal_funds": (proposal.funds + proposal.stake).total_funds(),
                }

                TRANSACTIONS.append(transaction)

                n_left += 1
                funds_claimed += wallet_funds_new - wallet_funds_old
            
    return {
        "n_left": n_left,
        "funds_claimed": funds_claimed,
    }


def p_pay(params, substep, state_history, previous_state):
    n_paid = 0
    funds_contributed = 0

    for wallet in WALLETS.values():
        for proposal in np.extract(params["pay"](wallet, len(PROPOSALS), y_scale=0.01), list(PROPOSALS.values())):
            wallet_funds_old = wallet.funds.total_funds()
            proposal_funds_old = (proposal.funds + proposal.stake).total_funds()
            
            contribution = params["pay_contribution"](wallet)
            
            wallet = proposal.pay(wallet, contribution)
            wallet_funds_new = wallet.funds.total_funds()
            
            if wallet_funds_new != wallet_funds_old:
                transaction = {
                    "timestep": previous_state["timestep"],
                    "wallet": wallet.public,
                    "wallet_funds_old": wallet_funds_old,
                    "wallet_funds": wallet_funds_new,
                    "action": "pay",
                    "proposal": proposal.public,
                    "proposal_funds_old": proposal_funds_old,
                    "proposal_funds": (proposal.funds + proposal.stake).total_funds(),
                }

                TRANSACTIONS.append(transaction)

                n_paid += 1
                funds_contributed += wallet_funds_new - wallet_funds_old
    
    return {
        "n_paid": n_paid,
        "funds_contributed": funds_contributed
    }


def p_vote(params, substep, state_history, previous_state):
    n_voted = 0
    voted_yes = 0
    
    for wallet in WALLETS.values():
        for proposal in np.extract(params["vote"](wallet, len(PROPOSALS), 1), list(PROPOSALS.values())):
            broker = WALLETS[params["vote_broker"](wallet)]
            result = params["vote_result"](wallet)
            
            proposal.vote_broker(wallet, broker, result)
            
            n_voted += 1
            voted_yes += result * 1
            
    return {
        "n_voted": n_voted,
        "voted_yes": voted_yes,
    }


def p_deploy(params, substep, state_history, previous_state):
    n_deployed = 0
    funds_contributed = 0
    
    for wallet in WALLETS.values():
        if params["deploy"](wallet, 1, y_scale=0.05)[0]:
            wallet_funds_old = wallet.funds.total_funds()
            initial_funds = params["deploy_initial_funds"](wallet)
            
            proposal = wallet.deploy(
                funds=initial_funds,
                broker_whitelist=NoVote(),
                feature_vector=rng.random(size=wallet.number_of_features)
            )
            
            if proposal is not None:
                PROPOSALS[proposal.public] = proposal
                
                transaction = {
                    "timestep": previous_state["timestep"],
                    "wallet": wallet.public,
                    "wallet_funds_old": wallet_funds_old,
                    "wallet_funds": wallet.funds.total_funds(),
                    "action": "deploy",
                    "proposal": proposal.public,
                    "proposal_funds_old": 0,
                    "proposal_funds": proposal.funds.total_funds(),
                }
            
                TRANSACTIONS.append(transaction)
            
                n_deployed += 1
                funds_contributed += initial_funds.total_funds()
        
    return {
        "n_deployed": n_deployed,
        "funds_contributed": funds_contributed
    }


def p_cancel(params, substep, state_history, previous_state):
    n_cancelled = 0
    n_left = 0
    
    for wallet in WALLETS.values():
        for proposal in np.extract(params["cancel"](wallet, len(PROPOSALS)), list(PROPOSALS.values())):
            wallet_funds_old = wallet.funds.total_funds()
            proposal_funds_old = (proposal.funds + proposal.stake).total_funds()
            
            proposal.cancel(wallet.public)
            
            for broker in list(proposal.broker_agreements.keys()):
                WALLETS[broker] = proposal.leave(WALLETS[broker])
                
                transaction = {
                    "timestep": previous_state["timestep"],
                    "wallet": broker,
                    "wallet_funds_old": wallet_funds_old,
                    "wallet_funds": WALLETS[broker].funds.total_funds(),
                    "action": "leave",
                    "proposal": proposal,
                    "proposal_funds_old": proposal_funds_old,
                    "proposal_funds": proposal.funds.total_funds(),
                }
            
                TRANSACTIONS.append(transaction)
                
                n_left += 1
                
            n_cancelled += 1
            
    return {
        "n_cancelled": n_cancelled,
        "n_left": n_left,
    }

## 4. State Update Functions

In [9]:
def s_total_funds(params, substep, state_history, previous_state, policy_input):
    wallet_funds = sum([wallet.funds for wallet in WALLETS.values()], Funds())
    proposal_funds = sum([proposal.funds + proposal.stake for proposal in PROPOSALS.values()], Funds())
    
    return "total_funds", wallet_funds.total_funds() + proposal_funds.total_funds()


def s_wallet_funds(params, substep, state_history, previous_state, policy_input):
    return "wallet_funds", sum([wallet.funds for wallet in WALLETS.values()], Funds()).total_funds()


def s_proposal_funds(params, substep, state_history, previous_state, policy_input):
    return "proposal_funds", sum([proposal.funds for proposal in PROPOSALS.values()], Funds()).total_funds()


def s_n_proposals(params, substep, state_history, previous_state, policy_input):
    return "n_proposals", len(PROPOSALS)


def s_owners(params, substep, state_history, previous_state, policy_input):
    n_owners = previous_state["owners"] + policy_input["n_deployed"] - policy_input["n_cancelled"]
    
    return "owners", n_owners


def s_payers(params, substep, state_history, previous_state, policy_input):
    n_payers = previous_state["payers"] + policy_input["n_paid"]
    
    return "payers", n_payers


def s_brokers(params, substep, state_history, previous_state, policy_input):
    n_brokers = previous_state["brokers"] + policy_input["n_joined"] - policy_input["n_left"]
    
    return "brokers", n_brokers


def s_funds_staked(params, substep, state_history, previous_state, policy_input):
    funds_staked = previous_state["funds_staked"] + policy_input["funds_staked"]
    
    return "funds_staked", funds_staked


def s_funds_claimed(params, substep, state_history, previous_state, policy_input):
    funds_claimed = previous_state["funds_claimed"] + policy_input["funds_claimed"]
    
    return "funds_claimed", funds_claimed


def s_funds_contributed(params, substep, state_history, previous_state, policy_input):
    funds_contributed = previous_state["funds_contributed"] + policy_input["funds_contributed"]
    
    return "funds_contributed", funds_contributed

## 5. Partial State Update Blocks

In [10]:
partial_state_update_blocks = [
    # Go to next epoch
    {
        "policies": {
            "iter_epoch": p_iter_epoch,
            "iter_features": p_iter_features,
        },
        "variables": {
        },
    },
    # Agents perform actions
    {   
        "policies": {
            "join": p_join,
            "claim": p_claim,
            "leave": p_leave,
            "pay": p_pay,
            "vote": p_vote,
            "deploy": p_deploy,
            "cancel": p_cancel,
        },
        'variables': {
            "total_funds": s_total_funds,
            "wallet_funds": s_wallet_funds,
            "proposal_funds": s_proposal_funds,
            "n_proposals": s_n_proposals,
            
            # Distribution of agent actions
            "owners": s_owners,
            "payers": s_payers,
            "brokers": s_brokers,
            
            # Proposal properties
            "funds_staked": s_funds_staked,
            "funds_claimed": s_funds_claimed,
            "funds_contributed": s_funds_contributed,
        }
    }
]

# Simulation

## 6. Configuration

In [11]:
sim_config = config_sim({
    "N": 1, # the number of times we'll run the simulation ("Monte Carlo runs")
    "T": range(100), # the number of timesteps the simulation will run for
    "M": system_params # the parameters of the system
})

In [12]:
experiment = Experiment()
experiment.append_configs(
    initial_state = initial_state,
    partial_state_update_blocks = partial_state_update_blocks,
    sim_configs = sim_config
)

## 7. Execution

In [13]:
exec_context = ExecutionContext()
simulation = Executor(exec_context=exec_context, configs=configs)
raw_result, tensor_field, sessions = simulation.execute()


                  ___________    ____
  ________ __ ___/ / ____/   |  / __ \
 / ___/ __` / __  / /   / /| | / / / /
/ /__/ /_/ / /_/ / /___/ ___ |/ /_/ /
\___/\__,_/\__,_/\____/_/  |_/_____/
by cadCAD

Execution Mode: local_proc
Configuration Count: 1
Dimensions of the first simulation: (Timesteps, Params, Runs, Vars) = (100, 13, 1, 11)
Execution Method: local_simulations
SimIDs   : [0]
SubsetIDs: [0]
Ns       : [0]
ExpIDs   : [0]
Execution Mode: single_threaded
Epoch: 0
ProposalInverter :: proposal deployed without meeting minimum conditions
Epoch: 1
ProposalInverter :: proposal deployed without meeting minimum conditions
ProposalInverter :: proposal deployed without meeting minimum conditions
Epoch: 2
Payer is not part of this proposal
Broker is not part of this proposal
ProposalInverter :: proposal deployed without meeting minimum conditions
Epoch: 3
Payer is not part of this proposal
Payer is not part of this proposal
Payer is not part of this proposal
Broker is not part of this p

Payer is not part of this proposal
Payer is not part of this proposal
Payer is not part of this proposal
Payer is not part of this proposal
Payer is not part of this proposal
Payer is not part of this proposal
Payer is not part of this proposal
Payer is not part of this proposal
Payer is not part of this proposal
Payer is not part of this proposal
Payer is not part of this proposal
Payer is not part of this proposal
Payer is not part of this proposal
Payer is not part of this proposal
Payer is not part of this proposal
Payer is not part of this proposal
Payer is not part of this proposal
Payer is not part of this proposal
Payer is not part of this proposal
Payer is not part of this proposal
Payer is not part of this proposal
Payer is not part of this proposal
Payer is not part of this proposal
Payer is not part of this proposal
Payer is not part of this proposal
Payer is not part of this proposal
Payer is not part of this proposal
Payer is not part of this proposal
Payer is not part of

Epoch: 15
Failed to add broker, broker already has a stake in this proposal
Failed to add broker, maximum number of brokers reached
Failed to add broker, maximum number of brokers reached
Failed to add broker, broker already has a stake in this proposal
Failed to add broker, maximum number of brokers reached
Failed to add broker, broker already has a stake in this proposal
Failed to add broker, broker already has a stake in this proposal
Failed to add broker, maximum number of brokers reached
Failed to add broker, broker already has a stake in this proposal
Failed to add broker, broker already has a stake in this proposal
Failed to add broker, maximum number of brokers reached
Failed to add broker, broker already has a stake in this proposal
Payer is not part of this proposal
Payer is not part of this proposal
Payer is not part of this proposal
Payer is not part of this proposal
Payer is not part of this proposal
Payer is not part of this proposal
Payer is not part of this proposal
Pay

ProposalInverter :: proposal deployed without meeting minimum conditions
ProposalInverter :: proposal deployed without meeting minimum conditions
ProposalInverter :: proposal deployed without meeting minimum conditions
ProposalInverter :: proposal deployed without meeting minimum conditions
Epoch: 18
Failed to add broker, maximum number of brokers reached
Failed to add broker, maximum number of brokers reached
Failed to add broker, maximum number of brokers reached
Failed to add broker, maximum number of brokers reached
Failed to add broker, maximum number of brokers reached
Failed to add broker, maximum number of brokers reached
Failed to add broker, maximum number of brokers reached
Failed to add broker, maximum number of brokers reached
Failed to add broker, maximum number of brokers reached
Failed to add broker, maximum number of brokers reached
Failed to add broker, maximum number of brokers reached
Failed to add broker, maximum number of brokers reached
Failed to add broker, maxi

Proposal has been cancelled, cannot add funds
Proposal has been cancelled, cannot add funds
ProposalInverter :: proposal deployed without meeting minimum conditions
ProposalInverter :: proposal deployed without meeting minimum conditions
ProposalInverter :: proposal deployed without meeting minimum conditions
Epoch: 20
Failed to add broker, maximum number of brokers reached
Failed to add broker, maximum number of brokers reached
Failed to add broker, maximum number of brokers reached
Failed to add broker, broker already has a stake in this proposal
Failed to add broker, proposal has been cancelled
Failed to add broker, broker already has a stake in this proposal
Failed to add broker, maximum number of brokers reached
Failed to add broker, maximum number of brokers reached
Failed to add broker, proposal has been cancelled
Failed to add broker, maximum number of brokers reached
Failed to add broker, maximum number of brokers reached
Failed to add broker, maximum number of brokers reached

...

Proposal has been cancelled, cannot add funds
Proposal has been cancelled, cannot add funds
Proposal has been cancelled, cannot add funds
Proposal has been cancelled, cannot add funds
Proposal has been cancelled, cannot add funds
Proposal has been cancelled, cannot add funds
Proposal has been cancelled, cannot add funds
Proposal has been cancelled, cannot add funds
Proposal has been cancelled, cannot add funds
Proposal has been cancelled, cannot add funds
ProposalInverter :: proposal deployed without meeting minimum conditions
ProposalInverter :: proposal deployed without meeting minimum conditions
Epoch: 97
Failed to add broker, maximum number of brokers reached
Failed to add broker, proposal has been cancelled
Failed to add broker, proposal has been cancelled
Failed to add broker, maximum number of brokers reached
Failed to add broker, maximum number of brokers reached
Failed to add broker, proposal has been cancelled
Failed to add broker, proposal has been cancelled
Failed to add br

ProposalInverter :: proposal deployed without meeting minimum conditions
Epoch: 98
Failed to add broker, maximum number of brokers reached
Failed to add broker, maximum number of brokers reached
Failed to add broker, maximum number of brokers reached
Failed to add broker, maximum number of brokers reached
Failed to add broker, maximum number of brokers reached
Failed to add broker, maximum number of brokers reached
Failed to add broker, maximum number of brokers reached
Failed to add broker, maximum number of brokers reached
Failed to add broker, maximum number of brokers reached
Failed to add broker, maximum number of brokers reached
Failed to add broker, maximum number of brokers reached
Failed to add broker, maximum number of brokers reached
Failed to add broker, maximum number of brokers reached
Failed to add broker, maximum number of brokers reached
Failed to add broker, broker already has a stake in this proposal
Failed to add broker, maximum number of brokers reached
Failed to a

Payer is not part of this proposal
Payer is not part of this proposal
Payer is not part of this proposal
Payer is not part of this proposal
Payer is not part of this proposal
Payer is not part of this proposal
Payer is not part of this proposal
Payer is not part of this proposal
Payer is not part of this proposal
Payer is not part of this proposal
Payer is not part of this proposal
Payer is not part of this proposal
Payer is not part of this proposal
Payer is not part of this proposal
Payer is not part of this proposal
Payer is not part of this proposal
Payer is not part of this proposal
Payer is not part of this proposal
Payer is not part of this proposal
Payer is not part of this proposal
Payer is not part of this proposal
Payer is not part of this proposal
Payer is not part of this proposal
Payer is not part of this proposal
Payer is not part of this proposal
Payer is not part of this proposal
Payer is not part of this proposal
Payer is not part of this proposal
Payer is not part of

Epoch: 99
Failed to add broker, proposal has been cancelled
Failed to add broker, proposal has been cancelled
Failed to add broker, proposal has been cancelled
Failed to add broker, maximum number of brokers reached
Failed to add broker, maximum number of brokers reached
Failed to add broker, maximum number of brokers reached
Failed to add broker, maximum number of brokers reached
Failed to add broker, maximum number of brokers reached
Failed to add broker, maximum number of brokers reached
Failed to add broker, proposal has been cancelled
Failed to add broker, broker already has a stake in this proposal
Failed to add broker, broker already has a stake in this proposal
Failed to add broker, broker already has a stake in this proposal
Failed to add broker, maximum number of brokers reached
Failed to add broker, maximum number of brokers reached
Failed to add broker, maximum number of brokers reached
Failed to add broker, maximum number of brokers reached
Failed to add broker, broker alr

Proposal has been cancelled, cannot add funds
Proposal has been cancelled, cannot add funds
Proposal has been cancelled, cannot add funds
Proposal has been cancelled, cannot add funds
Proposal has been cancelled, cannot add funds
ProposalInverter :: proposal deployed without meeting minimum conditions
ProposalInverter :: proposal deployed without meeting minimum conditions
ProposalInverter :: proposal deployed without meeting minimum conditions
Total execution time: 22.21s


## 8. Output Preparation

In [14]:
# Convert raw results to a Pandas DataFrame
df = pd.DataFrame(raw_result)

In [15]:
fdf = df[df["substep"] == 2]
fdf

total_funds  wallet_funds  proposal_funds  n_wallets  n_proposals  \
2       500000.0      499900.0           100.0         50            1   
4       500000.0      499650.0           350.0         50            3   
6       500000.0      499540.0           450.0         50            4   
8       500000.0      499430.0           540.0         50            4   
10      500000.0      499360.0           570.0         50            4   
..           ...           ...             ...        ...          ...   
192     500000.0      457090.0         35850.0         50          172   
194     500000.0      455910.0         36980.0         50          174   
196     500000.0      455740.0         37120.0         50          175   
198     500000.0      455500.0         37410.0         50          175   
200     500000.0      454920.0         37930.0         50          178   

     owners  payers  brokers  funds_staked  funds_claimed  funds_contributed  \
2         1       0        0           0.0            0.0              100.0   
4         3       1        0           0.0            0.0              250.0   
6         4       1        1          10.0            0.0              350.0   
8         4       3        3          30.0           10.0              250.0   
10        4       4        7          70.0           30.0              200.0   
..      ...     ...      ...           ...            ...                ...   
192     172    1426      875       10440.0        56030.0           -54100.0   
194     174    1464      882       10550.0        57060.0           -55800.0   
196     175    1484      889       10670.0        58110.0           -56700.0   
198     175    1512      886       10730.0        59330.0           -58100.0   
200     178    1536      894       10860.0        60380.0           -59000.0   

     simulation  subset  run  substep  timestep  
2             0       0    1        2         1  
4             0       0    1        2         2  
6             0       0    1        2         3  
8             0       0    1        2         4  
10            0       0    1        2         5  
..          ...     ...  ...      ...       ...  
192           0       0    1        2        96  
194           0       0    1        2        97  
196           0       0    1        2        98  
198           0       0    1        2        99  
200           0       0    1        2       100  

[100 rows x 16 columns]

In [16]:
# Insert cadCAD parameters for each configuration into DataFrame
for config in configs:
    # Get parameters from configuration
    parameters = config.sim_config['M']
    # Get subset index from configuration
    subset_index = config.subset_id
    
    # For each parameter key value pair
    for (key, value) in parameters.items():
        # Select all DataFrame indices where subset == subset_index
        dataframe_indices = df.eval(f'subset == {subset_index}')
        # Assign each parameter key value pair to the DataFrame for the corresponding subset
        df.loc[dataframe_indices, key] = value

df.head(10)

total_funds  wallet_funds  proposal_funds  n_wallets  n_proposals  owners  \
0     500000.0      500000.0             0.0         50            0       0   
1     500000.0      500000.0             0.0         50            0       0   
2     500000.0      499900.0           100.0         50            1       1   
3     500000.0      499900.0           100.0         50            1       1   
4     500000.0      499650.0           350.0         50            3       3   
5     500000.0      499650.0           350.0         50            3       3   
6     500000.0      499540.0           450.0         50            4       4   
7     500000.0      499540.0           450.0         50            4       4   
8     500000.0      499430.0           540.0         50            4       4   
9     500000.0      499430.0           540.0         50            4       4   

   payers  brokers  funds_staked  funds_claimed  ...  \
0       0        0           0.0            0.0  ...   
1       0        0           0.0            0.0  ...   
2       0        0           0.0            0.0  ...   
3       0        0           0.0            0.0  ...   
4       1        0           0.0            0.0  ...   
5       1        0           0.0            0.0  ...   
6       1        1          10.0            0.0  ...   
7       1        1          10.0            0.0  ...   
8       3        3          30.0           10.0  ...   
9       3        3          30.0           10.0  ...   

                                             leave  \
0  <function a_static_1_percent at 0x7f83ff1dd900>   
1  <function a_static_1_percent at 0x7f83ff1dd900>   
2  <function a_static_1_percent at 0x7f83ff1dd900>   
3  <function a_static_1_percent at 0x7f83ff1dd900>   
4  <function a_static_1_percent at 0x7f83ff1dd900>   
5  <function a_static_1_percent at 0x7f83ff1dd900>   
6  <function a_static_1_percent at 0x7f83ff1dd900>   
7  <function a_static_1_percent at 0x7f83ff1dd900>   
8  <function a_static_1_percent at 0x7f83ff1dd900>   
9  <function a_static_1_percent at 0x7f83ff1dd900>   

                                                pay  \
0  <function a_increasing_linear at 0x7f83ff1de320>   
1  <function a_increasing_linear at 0x7f83ff1de320>   
2  <function a_increasing_linear at 0x7f83ff1de320>   
3  <function a_increasing_linear at 0x7f83ff1de320>   
4  <function a_increasing_linear at 0x7f83ff1de320>   
5  <function a_increasing_linear at 0x7f83ff1de320>   
6  <function a_increasing_linear at 0x7f83ff1de320>   
7  <function a_increasing_linear at 0x7f83ff1de320>   
8  <function a_increasing_linear at 0x7f83ff1de320>   
9  <function a_increasing_linear at 0x7f83ff1de320>   

                                            vote  \
0  <function a_dynamic_funded at 0x7f83ff1de200>   
1  <function a_dynamic_funded at 0x7f83ff1de200>   
2  <function a_dynamic_funded at 0x7f83ff1de200>   
3  <function a_dynamic_funded at 0x7f83ff1de200>   
4  <function a_dynamic_funded at 0x7f83ff1de200>   
5  <function a_dynamic_funded at 0x7f83ff1de200>   
6  <function a_dynamic_funded at 0x7f83ff1de200>   
7  <function a_dynamic_funded at 0x7f83ff1de200>   
8  <function a_dynamic_funded at 0x7f83ff1de200>   
9  <function a_dynamic_funded at 0x7f83ff1de200>   

                                  deploy  \
0  <function a_normal at 0x7f83ff1de3b0>   
1  <function a_normal at 0x7f83ff1de3b0>   
2  <function a_normal at 0x7f83ff1de3b0>   
3  <function a_normal at 0x7f83ff1de3b0>   
4  <function a_normal at 0x7f83ff1de3b0>   
5  <function a_normal at 0x7f83ff1de3b0>   
6  <function a_normal at 0x7f83ff1de3b0>   
7  <function a_normal at 0x7f83ff1de3b0>   
8  <function a_normal at 0x7f83ff1de3b0>   
9  <function a_normal at 0x7f83ff1de3b0>   

                                            cancel  \
0  <function a_static_0_percent at 0x7f83ff1dd750>   
1  <function a_static_0_percent at 0x7f83ff1dd750>   
2  <function a_static_0_percent at 0x7f83ff1dd750>   
3  <function a_static_0_percen

In [17]:
transactions_df = pd.DataFrame(TRANSACTIONS)
transactions_df.to_csv("transactions.csv", header=True, index=False)
transactions_df

timestep                                      wallet  wallet_funds  \
0             0  0x09891B11608d1BdC2EAC5651Ec3EefF15f5765B9  14460.177801   
1             0  0x7c69773795d70d41d8Ca4285Ac5218561BCe72f8   8199.768299   
2             0  0xca12Ac68Dc6E25980811A9b609b1C8ADc2239C9d  16041.580920   
3             0  0x439e3E16576dF3efdE37dcfEee5028883C2f0367  13029.248510   
4             0  0x2278E9b946b5BA06BbE83810D075d60D07B69844   1759.558825   
...         ...                                         ...           ...   
28478       100  0xcdC417286c462A7794863c1d565139Ee29eC82A5   6453.270592   
28479       100  0x9F9C932D07Faf5113582c63C14577C3b8560Db89   5702.633608   
28480       100  0x6Da4CC422c13f017dF13f8B2B0ABFE57e6f4885F  11520.401507   
28481       100  0x1F887138Ce3dBDb70106bfe92344eA5935d270c2   6647.636209   
28482       100  0x3d77632b1A4e653637c18b932d50473821526f74  10719.044932   

           action  wallet_funds_old  \
0      initialize               NaN   
1      initialize               NaN   
2      initialize               NaN   
3      initialize               NaN   
4      initialize               NaN   
...           ...               ...   
28478         pay       6503.270592   
28479         pay       5752.633608   
28480      deploy      11620.401507   
28481      deploy       6747.636209   
28482      deploy      10819.044932   

                                         proposal  proposal_funds_old  \
0                                             NaN                 NaN   
1                                             NaN                 NaN   
2                                             NaN                 NaN   
3                                             NaN                 NaN   
4                                             NaN                 NaN   
...                                           ...                 ...   
28478  0x7dFef7c3b76EBec0C495C6A62D7ffBBADB85e0bF               760.0   
28479  0x4d7752dc405A23AD26990F4e828Bc71bbd9CA88C               640.0   
28480  0xbcfe22906B41C9C90cF974d8073958b6BB1fe4A5                 0.0   
28481  0xcAD999086ec6E931A02f26dAFee1C916B5b2c0e9                 0.0   
28482  0x41Ad6AcF9D49A88d490d514E9e2e1fF22520dBf2                 0.0   

       proposal_funds  
0                 NaN  
1                 NaN  
2                 NaN  
3                 NaN  
4                 NaN  
...               ...  
28478           810.0  
28479           690.0  
28480           100.0  
28481           100.0  
28482           100.0  

[28483 rows x 8 columns]

## 9. Analysis

## 9.1 Distribution of Actions

In [18]:
actions = transactions_df.pivot_table(columns=["action"], aggfunc="size")
actions

action
claim         25441
deploy          178
initialize       50
join           1086
leave           192
pay            1536
dtype: int64

In [42]:
actions.plot(
    kind="bar",
    title="Distribution of Actions"
)

## 9.2 Wallets

In [20]:
# timestep, wallet1, wallet2, ...
wfunds_df = pd.DataFrame({"timestep": sim_config[0]["T"]})

for public, wallet in WALLETS.items():
    wallet_df = transactions_df[transactions_df["wallet"] == public]
    wallet_df = wallet_df[["timestep", "wallet_funds"]]
    wallet_df = wallet_df.drop_duplicates(subset="timestep", keep="last")
    
    wallet_df.columns = ["timestep", wallet.public]
    wfunds_df = pd.merge(wfunds_df, wallet_df, how="outer", on="timestep")
    
wfunds_df = wfunds_df.fillna(method="ffill")
wfunds_df

timestep  0x09891B11608d1BdC2EAC5651Ec3EefF15f5765B9  \
0           0                                14460.177801   
1           1                                14460.177801   
2           2                                14460.177801   
3           3                                14460.177801   
4           4                                14460.177801   
..        ...                                         ...   
96         96                                12076.844467   
97         97                                12088.844467   
98         98                                12050.844467   
99         99                                12012.844467   
100       100                                12024.844467   

     0x7c69773795d70d41d8Ca4285Ac5218561BCe72f8  \
0                                   8199.768299   
1                                   8199.768299   
2                                   8199.768299   
3                                   8199.768299   
4                                   8199.768299   
..                                          ...   
96                                  7777.434966   
97                                  7747.434966   
98                                  7779.934966   
99                                  7811.934966   
100                                 7833.934966   

     0xca12Ac68Dc6E25980811A9b609b1C8ADc2239C9d  \
0                                  16041.580920   
1                                  16041.580920   
2                                  16041.580920   
3                                  16041.580920   
4                                  16041.580920   
..                                          ...   
96                                 14132.414253   
97                                 14090.414253   
98                                 14098.414253   
99                                 14046.414253   
100                                14056.414253   

     0x439e3E16576dF3efdE37dcfEee5028883C2f0367  \
0                                   13029.24851   
1                                   13029.24851   
2                                   13029.24851   
3                                   13029.24851   
4                                   13029.24851   
..                                          ...   
96                                  11861.24851   
97                                  11833.24851   
98                                  11845.24851   
99                                  11757.24851   
100                                 11719.24851   

     0x2278E9b946b5BA06BbE83810D075d60D07B69844  \
0                                   1759.558825   
1                                   1759.558825   
2                                   1759.558825   
3                                   1759.558825   
4                                   1759.558825   
..                                          ...   
96                                  3652.392158   
97                                  3693.892158   
98                                  3688.225491   
99                                  3747.558825   
100                                 3804.892158   

     0xF162Bd063afE34038bfD03DD9f428549f8448338  \
0                                  18228.002349   
1                                  18228.002349   
2                                  18228.002349   
3                                  18228.002349   
4                                  18228.002349   
..                                          ...   
96                                 15138.502349   
97                                 14990.502349   
98                                 14842.502349   
99                                 14794.502349   
100                                14796.502349   

     0xAe15e978ed2F5957Bcf4e616381088bb9Eb27e14  \
0                                  14220.724087   
1                                  14220.724087   
2                                  14220.724087   
3  

In [21]:
wfunds_df.plot(
    x="timestep", 
    y=list(WALLETS.keys()), 
    title="Wallet Funds"
)

In [22]:
# Positions show how much each wallet made relative to their initial value
wpositions_df = wfunds_df.copy()

initial_funds = np.array(wpositions_df[wfunds_df["timestep"] == 0][list(WALLETS.keys())])
wpositions_df[list(WALLETS.keys())] = wpositions_df[list(WALLETS.keys())].sub(initial_funds)

wpositions_df

timestep  0x09891B11608d1BdC2EAC5651Ec3EefF15f5765B9  \
0           0                                    0.000000   
1           1                                    0.000000   
2           2                                    0.000000   
3           3                                    0.000000   
4           4                                    0.000000   
..        ...                                         ...   
96         96                                -2383.333333   
97         97                                -2371.333333   
98         98                                -2409.333333   
99         99                                -2447.333333   
100       100                                -2435.333333   

     0x7c69773795d70d41d8Ca4285Ac5218561BCe72f8  \
0                                      0.000000   
1                                      0.000000   
2                                      0.000000   
3                                      0.000000   
4                                      0.000000   
..                                          ...   
96                                  -422.333333   
97                                  -452.333333   
98                                  -419.833333   
99                                  -387.833333   
100                                 -365.833333   

     0xca12Ac68Dc6E25980811A9b609b1C8ADc2239C9d  \
0                                      0.000000   
1                                      0.000000   
2                                      0.000000   
3                                      0.000000   
4                                      0.000000   
..                                          ...   
96                                 -1909.166667   
97                                 -1951.166667   
98                                 -1943.166667   
99                                 -1995.166667   
100                                -1985.166667   

     0x439e3E16576dF3efdE37dcfEee5028883C2f0367  \
0                                           0.0   
1                                           0.0   
2                                           0.0   
3                                           0.0   
4                                           0.0   
..                                          ...   
96                                      -1168.0   
97                                      -1196.0   
98                                      -1184.0   
99                                      -1272.0   
100                                     -1310.0   

     0x2278E9b946b5BA06BbE83810D075d60D07B69844  \
0                                      0.000000   
1                                      0.000000   
2                                      0.000000   
3                                      0.000000   
4                                      0.000000   
..                                          ...   
96                                  1892.833333   
97                                  1934.333333   
98                                  1928.666667   
99                                  1988.000000   
100                                 2045.333333   

     0xF162Bd063afE34038bfD03DD9f428549f8448338  \
0                                           0.0   
1                                           0.0   
2                                           0.0   
3                                           0.0   
4                                           0.0   
..                                          ...   
96                                      -3089.5   
97                                      -3237.5   
98                                      -3385.5   
99                                      -3433.5   
100                                     -3431.5   

     0xAe15e978ed2F5957Bcf4e616381088bb9Eb27e14  \
0                                      0.000000   
1                                      0.000000   
2                                      0.000000   
3  

In [34]:
wpositions_df.plot(
    x="timestep", 
    y=list(WALLETS.keys()), 
    title="Wallet Positions"
)

## 9.3 Proposals

In [24]:
# timestep, proposal1, proposal2, ...
pfunds_df = pd.DataFrame({"timestep": sim_config[0]["T"]})

for public, proposal in PROPOSALS.items():
    proposal_df = transactions_df[transactions_df["proposal"] == public]
    proposal_df = proposal_df[["timestep", "proposal_funds"]]
    proposal_df = proposal_df.drop_duplicates(subset="timestep", keep="last")
    
    proposal_df.columns = ["timestep", proposal.public]
    pfunds_df = pd.merge(pfunds_df, proposal_df, how="outer", on="timestep")
    
pfunds_df = pfunds_df.fillna(method="ffill")
pfunds_df

timestep  0xB76656107AA42dEC0C6823E6529EB8ED62adf1Be  \
0           0                                         NaN   
1           1                                       100.0   
2           2                                       150.0   
3           3                                       150.0   
4           4                                       200.0   
..        ...                                         ...   
96         96                                       330.0   
97         97                                       320.0   
98         98                                       360.0   
99         99                                       450.0   
100       100                                       450.0   

     0x2B7B5Bd31f80f020e42e110234Fa99BfD7533781  \
0                                           NaN   
1                                           NaN   
2                                         100.0   
3                                         110.0   
4                                         110.0   
..                                          ...   
96                                         20.0   
97                                         20.0   
98                                         20.0   
99                                         20.0   
100                                        20.0   

     0x3A61981e8976Bb9DfDa9c702A6B0226220ccad9E  \
0                                           NaN   
1                                           NaN   
2                                         100.0   
3                                         100.0   
4                                         150.0   
..                                          ...   
96                                        470.0   
97                                        610.0   
98                                        600.0   
99                                        690.0   
100                                       730.0   

     0xC75445c45fAEBa52A05eb1C5120A6C1C9C05694b  \
0                                           NaN   
1                                           NaN   
2                                           NaN   
3                                         100.0   
4                                         110.0   
..                                          ...   
96                                         40.0   
97                                         40.0   
98                                         40.0   
99                                         30.0   
100                                        30.0   

     0xf6f2f374a4C526901aa7E787837141eF7ce6ac6a  \
0                                           NaN   
1                                           NaN   
2                                           NaN   
3                                           NaN   
4                                           NaN   
..                                          ...   
96                                         30.0   
97                                         30.0   
98                                         30.0   
99                                         30.0   
100                                        30.0   

     0x51fBF8352548e0E6687F6C7Cc23b3732AAC5397b  \
0                                           NaN   
1                                           NaN   
2                                           NaN   
3                                           NaN   
4                                           NaN   
..                                          ...   
96                                        540.0   
97                                        530.0   
98                                        520.0   
99                                        510.0   
100                                       500.0   

     0x2ee0562CC31A971d5BD090759528e69f42D852fB  \
0                                           NaN   
1                                           NaN   
2                                           NaN   
3  

In [36]:
pfunds_df.plot(
    x="timestep", 
    y=[key for key, value in PROPOSALS.items() if value.funds.total_funds() > 0], 
    title="Proposals with Funds"
)

In [37]:
pfunds_df.plot(
    x="timestep", 
    y=[key for key, value in PROPOSALS.items() if value.funds.total_funds() <= 0],
    title="Proposals with No Funds"
)

In [27]:
# Positions show how many funds each proposal has relative to its minimum horizon
ppositions_df = pfunds_df.copy()

min_horizons = pd.DataFrame(
    data=[[proposal.min_horizon * proposal.allocation_per_epoch for proposal in PROPOSALS.values()]],
    columns=list(PROPOSALS.keys())
)
# Why does this give nans?
#ppositions_df[list(PROPOSALS.keys())] = ppositions_df[list(PROPOSALS.keys())].sub(min_horizons)
ppositions_df[list(PROPOSALS.keys())] = ppositions_df[list(PROPOSALS.keys())].sub(70)

ppositions_df

timestep  0xB76656107AA42dEC0C6823E6529EB8ED62adf1Be  \
0           0                                         NaN   
1           1                                        30.0   
2           2                                        80.0   
3           3                                        80.0   
4           4                                       130.0   
..        ...                                         ...   
96         96                                       260.0   
97         97                                       250.0   
98         98                                       290.0   
99         99                                       380.0   
100       100                                       380.0   

     0x2B7B5Bd31f80f020e42e110234Fa99BfD7533781  \
0                                           NaN   
1                                           NaN   
2                                          30.0   
3                                          40.0   
4                                          40.0   
..                                          ...   
96                                        -50.0   
97                                        -50.0   
98                                        -50.0   
99                                        -50.0   
100                                       -50.0   

     0x3A61981e8976Bb9DfDa9c702A6B0226220ccad9E  \
0                                           NaN   
1                                           NaN   
2                                          30.0   
3                                          30.0   
4                                          80.0   
..                                          ...   
96                                        400.0   
97                                        540.0   
98                                        530.0   
99                                        620.0   
100                                       660.0   

     0xC75445c45fAEBa52A05eb1C5120A6C1C9C05694b  \
0                                           NaN   
1                                           NaN   
2                                           NaN   
3                                          30.0   
4                                          40.0   
..                                          ...   
96                                        -30.0   
97                                        -30.0   
98                                        -30.0   
99                                        -40.0   
100                                       -40.0   

     0xf6f2f374a4C526901aa7E787837141eF7ce6ac6a  \
0                                           NaN   
1                                           NaN   
2                                           NaN   
3                                           NaN   
4                                           NaN   
..                                          ...   
96                                        -40.0   
97                                        -40.0   
98                                        -40.0   
99                                        -40.0   
100                                       -40.0   

     0x51fBF8352548e0E6687F6C7Cc23b3732AAC5397b  \
0                                           NaN   
1                                           NaN   
2                                           NaN   
3                                           NaN   
4                                           NaN   
..                                          ...   
96                                        470.0   
97                                        460.0   
98                                        450.0   
99                                        440.0   
100                                       430.0   

     0x2ee0562CC31A971d5BD090759528e69f42D852fB  \
0                                           NaN   
1                                           NaN   
2                                           NaN   
3  

In [38]:
ppositions_df.plot(
    x="timestep", 
    y=[key for key, value in PROPOSALS.items() if value.funds.total_funds() > 0],
    title="Proposals with Funds Positions"
)

In [39]:
ppositions_df.plot(
    x="timestep", 
    y=[key for key, value in PROPOSALS.items() if value.funds.total_funds() <= 0],
    title="Proposals With No Funds Positions"
)

## 9.4 Claims

In [30]:
broker_holdings = dict()

for index, transaction in transactions_df.iterrows():
    if transaction["action"] == "claim":
        wallet = transaction["wallet"]
        
        if wallet not in broker_holdings.keys():
            broker_holdings[wallet] = {0: 0}
            
        broker_holdings[wallet][transaction["timestep"]] = max(broker_holdings[wallet].values()) + (transaction["wallet_funds"] - transaction["wallet_funds_old"])

broker_holdings_df = pd.DataFrame(broker_holdings)
broker_holdings_df = broker_holdings_df.sort_index()
broker_holdings_df = broker_holdings_df.fillna(method="ffill")
broker_holdings_df

0x1815013a8fb334469389412c637c90D455B8d3c0  \
0                                      0.000000   
4                                     10.000000   
5                                     15.000000   
6                                     18.333333   
7                                     20.833333   
..                                          ...   
96                                  2097.166667   
97                                  2147.166667   
98                                  2197.166667   
99                                  2259.666667   
100                                 2306.166667   

     0x0C2B120c7629fD567df7DF8909aDE4cF262E1749  \
0                                      0.000000   
4                                      0.000000   
5                                      5.000000   
6                                      8.333333   
7                                     10.833333   
..                                          ...   
96                                  1165.666667   
97                                  1193.000000   
98                                  1221.000000   
99                                  1254.000000   
100                                 1286.500000   

     0xb4eFB26E8cBFD8F8d3735578C8a788e3D18CD9eA  \
0                                      0.000000   
4                                      0.000000   
5                                     10.000000   
6                                     15.000000   
7                                     17.500000   
..                                          ...   
96                                  1432.166667   
97                                  1450.166667   
98                                  1468.166667   
99                                  1486.666667   
100                                 1504.666667   

     0xc31749995fcCf3373c94daD1e4e1e34c1734eFa6  \
0                                      0.000000   
4                                      0.000000   
5                                      0.000000   
6                                      5.000000   
7                                      7.000000   
..                                          ...   
96                                  2135.333333   
97                                  2173.333333   
98                                  2211.833333   
99                                  2263.333333   
100                                 2301.833333   

     0x88b4614436558c080B314033b532BA11576E1dBC  \
0                                           0.0   
4                                           0.0   
5                                           0.0   
6                                           5.0   
7                                           7.5   
..                                          ...   
96                                       1962.5   
97                                       1987.0   
98                                       2011.5   
99                                       2036.0   
100                                      2058.0   

     0xD816e8EA69495CcF63A0eeC2f706B4503bAA7c12  \
0                                      0.000000   
4                                      0.000000   
5                                      0.000000   
6                                      5.000000   
7                                      7.000000   
..                                          ...   
96                                   762.833333   
97                                   778.833333   
98                                   794.833333   
99                                   810.833333   
100                                  827.333333   

     0xD115Da0FEa518e72a36D87749a14f7b3EA185920  \
0                                      0.000000   
4                                      0.000000   
5                                      0.000000   
6                                      3.333333   
7                                      5.833333   
..                   

In [41]:
broker_holdings_df.plot(
    kind='area',
    title="Broker Claims over All Proposals"
)

In [32]:
for proposal in PROPOSALS.values():
    if len(proposal.broker_agreements) >= 5 and not proposal.cancelled:
        proposal_id = proposal.public
        break

broker_holdings = dict()

for index, transaction in transactions_df.iterrows():
    if transaction["proposal"] == proposal_id and transaction["action"] == "claim":
        wallet = transaction["wallet"]
        
        if wallet not in broker_holdings.keys():
            broker_holdings[wallet] = {0: 0}
            
        broker_holdings[wallet][transaction["timestep"]] = max(broker_holdings[wallet].values()) + (transaction["wallet_funds"] - transaction["wallet_funds_old"])

proposal_holdings_df = pd.DataFrame(broker_holdings)
proposal_holdings_df = proposal_holdings_df.sort_index()
proposal_holdings_df = proposal_holdings_df.fillna(method="ffill")
proposal_holdings_df

0xd7E9398f4F79B941DB3F3F3A69608C47fD9189Fa  \
0                                      0.000000   
9                                      3.333333   
10                                     5.333333   
11                                     7.333333   
12                                     9.333333   
..                                          ...   
96                                   178.833333   
97                                   180.833333   
98                                   182.833333   
99                                   184.833333   
100                                  187.333333   

     0xD115Da0FEa518e72a36D87749a14f7b3EA185920  \
0                                      0.000000   
9                                      3.333333   
10                                     5.333333   
11                                     7.333333   
12                                     9.333333   
..                                          ...   
96                                    17.333333   
97                                    17.333333   
98                                    17.333333   
99                                    17.333333   
100                                   17.333333   

     0x1F887138Ce3dBDb70106bfe92344eA5935d270c2  \
0                                      0.000000   
9                                      3.333333   
10                                     5.333333   
11                                     7.333333   
12                                     9.333333   
..                                          ...   
96                                   160.333333   
97                                   160.333333   
98                                   160.333333   
99                                   160.333333   
100                                  160.333333   

     0xE480fD34fF75DaC503b9005d3b184f246323F2a3  \
0                                           0.0   
9                                           0.0   
10                                          2.0   
11                                          4.0   
12                                          6.0   
..                                          ...   
96                                        173.0   
97                                        175.0   
98                                        177.0   
99                                        179.0   
100                                       179.0   

     0x9F9C932D07Faf5113582c63C14577C3b8560Db89  \
0                                           0.0   
9                                           0.0   
10                                          2.0   
11                                          4.0   
12                                          6.0   
..                                          ...   
96                                        175.5   
97                                        177.5   
98                                        179.5   
99                                        181.5   
100                                       184.0   

     0x2278E9b946b5BA06BbE83810D075d60D07B69844  \
0                                           0.0   
9                                           0.0   
10                                          0.0   
11                                          0.0   
12                                          0.0   
..                                          ...   
96                                        159.0   
97                                        161.0   
98                                        163.0   
99                                        165.0   
100                                       167.5   

     0xD816e8EA69495CcF63A0eeC2f706B4503bAA7c12  
0                                           0.0  
9                                           0.0  
10                                          0.0  
11                                          0.0  
12                                          0.0  
..                         

In [33]:
proposal_holdings_df.plot(kind='area', title="Claims In A Single Proposal")